In [1]:
pip install geopandas altair pandas jupyter

Note: you may need to restart the kernel to use updated packages.


# Task 1

In [2]:
import pandas as pd
import geopandas as gpd
import altair as alt
from shapely.geometry import Point

In [3]:
df = pd.read_csv('C:/Users/Yashith reddy/Desktop/UIC/CS 424 - Visualization and Visual Analytics/Lab/GeoPandas Lab/Taxi_Trips.csv')
geometry = [Point(xy) for xy in zip(df['Pickup Centroid Longitude'], df['Pickup Centroid Latitude'])]
gdf = gpd.GeoDataFrame(df, geometry=geometry, crs=4326).sample(1000)
gdf = gdf.rename(columns={"Trip Seconds": "Trip_Seconds", "Trip Miles": "Trip_Miles"})

In [4]:
gdf.head()

Trip ID  \
26955  63df603a8032d758abaac2dcca7f78754354f9ad   
37557  0068a9bea943309f543ef54a73386d4d33455100   
10129  c09ec91fa39e0b35edc6eb2e4ea4c1fe34462951   
70497  1afa35a0f00ca51f875251c35c0297c12329add7   
58259  f9041911f2b31ca3a2616ce631dbb5c23fbc7da0   

                                                 Taxi ID  \
26955  799deebf2f513dbebcad07d26fedd03920ea747cb97055...   
37557  d5606e39aadb36a16739062a2d6fe7f388118af055199e...   
10129  fe36f20fd7d241b5ac4e503b62d065f98b97bd8b8dcca5...   
70497  3eadc40f0f66886a6773acf85b7726e81975d9fb7ce971...   
58259  54ab53ea65bdfb30a1d764d23fa4f40261b6d8a657125a...   

         Trip Start Timestamp      Trip End Timestamp  Trip_Seconds  \
26955  07/05/2022 08:30:00 AM  07/05/2022 08:45:00 AM         900.0   
37557  07/05/2022 06:45:00 PM  07/05/2022 07:00:00 PM         900.0   
10129  07/03/2022 07:30:00 PM  07/03/2022 07:45:00 PM         525.0   
70497  07/07/2022 05:30:00 PM  07/07/2022 05:45:00 PM         633.0   
58259  07/07/2022 02:45:00 AM  07/07/2022 03:15:00 AM        1067.0   

       Trip_Miles  Pickup Census Tract  Dropoff Census Tract  \
26955        0.50                  NaN                   NaN   
37557        6.10                  NaN                   NaN   
10129        2.16                  NaN                   NaN   
70497        0.38         1.703108e+10          1.703108e+10   
58259        9.79                  NaN                   NaN   

       Pickup Community Area  Dropoff Community Area  ...  Trip Total  \
26955                   39.0                    28.0  ...       21.75   
37557                   32.0                    39.0  ...       18.25   
10129                    3.0                     6.0  ...       13.37   
70497                    8.0                     8.0  ...        7.75   
58259                   33.0                    56.0  ...       28.20   

       Payment Type                    Company  Pickup Centroid Latitude  \
26955       Unknown  Taxi Affiliation Services                 41.808916   
37557          Cash  Taxi Affiliation Services                 41.878866   
10129        Mobile               City Service                 41.965812   
70497          Cash               City Service                 41.892508   
58259          Cash                  Flash Cab                 41.857184   

       Pickup Centroid Longitude              Pickup Centroid Location  \
26955                 -87.596183  POINT (-87.5961833442 41.8089162826)   
37557                 -87.625192  POINT (-87.6251921424 41.8788655841)   
10129                 -87.655879    POINT (-87.6558787862 41.96581197)   
70497                 -87.626215  POINT (-87.6262149064 41.8925077809)   
58259                 -87.620335  POINT (-87.6203346241 41.8571838585)   

      Dropoff Centroid Latitude  Dropoff Centroid Longitude  \
26955                 41.874005                  -87.663518   
37557                 41.808916                  -87.596183   
10129                 41.944227                  -87.655998   
70497                 41.892508                  -87.626215   
58259                 41.792592                  -87.769615   

                 Dropoff Centroid  Location                    geometry  
26955   POINT (-87.6635175498 41.874005383)  POINT (-87.59618 41.80892)  
37557  POINT (-87.5961833442 41.8089162826)  POINT (-87.62519 41.87887)  
10129  POINT (-87.6559981815 41.9442266014)  POINT (-87.65588 41.96581)  
70497  POINT (-87.6262149064 41.8925077809)  POINT (-87.62621 41.89251)  
58259  POINT (-87.7696154528 41.7925923603)  POINT (-87.62033 41.85718)  

[5 rows x 24 columns]

# Task 2

In [5]:
chicago = gpd.read_file('C:/Users/Yashith reddy/Desktop/UIC/CS 424 - Visualization and Visual Analytics/Lab/GeoPandas Lab/chicago.geojson')

In [7]:
joined = gpd.sjoin(gdf, chicago, predicate='within')

In [9]:
joined['Fare'] = pd.to_numeric(joined['Fare'], errors='coerce')

In [10]:
joined = joined[['zip', 'Fare']]

In [11]:
joined = joined.groupby('zip', as_index=False).mean()

In [12]:
print(joined.isna().sum())

zip     0
Fare    0
dtype: int64


In [13]:
merged = chicago.merge(joined, on='zip')

# Task 3

In [14]:
brush = alt.selection_interval()

matrix = alt.Chart(gdf).mark_circle().add_params(brush).encode(
    alt.X(alt.repeat("column"), type='quantitative'),
    alt.Y(alt.repeat("row"), type='quantitative'),
    color=alt.condition(brush, 'Payment Type:N', alt.value('grey')),
    opacity=alt.condition(brush, alt.value(0.8), alt.value(0.1))
).properties(
    width=150,
    height=150
).repeat(
    row=['Fare', 'Trip_Miles', 'Trip_Seconds'],
    column=['Trip_Seconds', 'Trip_Miles', 'Fare']
)

matrix

alt.RepeatChart(...)

# Task 4

In [15]:
scatter = alt.Chart(gdf).mark_circle().encode(
    x=alt.Y('Pickup Centroid Longitude',scale=alt.Scale(domain=[-88.0, -87.5])),
    y=alt.Y('Pickup Centroid Latitude',scale=alt.Scale(domain=[41.6, 42.1])),
    color='Fare',
    opacity=alt.condition(brush, alt.value(1), alt.value(0))
)

In [16]:
brush = alt.selection_interval()
(scatter & matrix).add_params(brush)

alt.VConcatChart(...)

# Using Heatmap

In [40]:
import altair as alt

brush = alt.selection_interval()

heatmap_trip_seconds = alt.Chart(gdf).mark_rect().encode(
    x=alt.X('Pickup Centroid Longitude', bin=alt.Bin(maxbins=30)),
    y=alt.Y('Pickup Centroid Latitude', bin=alt.Bin(maxbins=30)),
    color=alt.Color('Trip_Seconds', scale=alt.Scale(scheme='reds')),
    opacity=alt.condition(brush, alt.value(1), alt.value(0.1))
).add_params(brush)


heatmap_trip_miles = alt.Chart(gdf).mark_rect().encode(
    x=alt.X('Pickup Centroid Longitude', bin=alt.Bin(maxbins=30)),
    y=alt.Y('Pickup Centroid Latitude', bin=alt.Bin(maxbins=30)),
    color=alt.Color('Trip_Miles', scale=alt.Scale(scheme='blues')),
    opacity=alt.condition(brush, alt.value(1), alt.value(0.1))
).add_params(brush)


heatmap_fare = alt.Chart(gdf).mark_rect().encode(
    x=alt.X('Pickup Centroid Longitude', bin=alt.Bin(maxbins=30)),
    y=alt.Y('Pickup Centroid Latitude', bin=alt.Bin(maxbins=30)),
    color=alt.Color('Fare', scale=alt.Scale(scheme='greens')),
    opacity=alt.condition(brush, alt.value(1), alt.value(0.1))
).add_params(brush)

heatmap_trip_seconds & heatmap_trip_miles & heatmap_fare

alt.VConcatChart(...)

In [41]:
import altair as alt

brush = alt.selection_interval()

heatmap = alt.Chart(gdf).mark_rect().encode(
    alt.X(alt.repeat("column"), bin=alt.Bin(maxbins=30)),
    alt.Y(alt.repeat("row"), bin=alt.Bin(maxbins=30)),
    color=alt.Color(alt.repeat("column"), scale=alt.Scale(scheme='reds')),
    opacity=alt.condition(brush, alt.value(1), alt.value(0.1))
).add_params(brush).properties(
    width=150,
    height=150
).repeat(
    row=['Fare', 'Trip_Miles', 'Trip_Seconds'],
    column=['Trip_Seconds', 'Trip_Miles', 'Fare']
)

heatmap

alt.RepeatChart(...)